# Working

## Plot annual velocity at point against time

In [208]:
import geopandas as gpd
import pandas as pd
import numpy as np
import xarray as xr

import glob
import re

GLACIERS = ["DJ", "UI"]

points = gpd.read_file("../data/misc/centreline_points.geojson")
points = points.sort_values(by=["glacier_code", "cd"]).reset_index()
points = points[points["cd"].between(0, 20000)].reset_index()
xs, ys = points.geometry.x.values, points.geometry.y.values

files = glob.glob("../data/velocity/*.nc")
pattern = re.compile(r"ITS_LIVE_velocity_120m_RGI05A_(\d{4})_v02\.nc")
annual_mosaics = [f for f in files if pattern.search(f)]
annual_mosaics = sorted(annual_mosaics[1:])
velocity = xr.open_mfdataset(
    annual_mosaics, concat_dim="year", combine="nested", chunks={"x": 1000, "y": 1000}
)

velocity_sampled = xr.Dataset(
    data_vars={
        "v_median": (("cd", "year"), np.empty((len(points.cd), len(velocity.year)))),
        "v_error_median": (
            ("cd", "year"),
            np.empty((len(points.cd), len(velocity.year))),
        ),
        "mapping": (("year"), velocity.mapping.values),
    },
    coords={
        "x": (("cd",), points.geometry.x),
        "y": (("cd",), points.geometry.y),
        "cd": (("cd",), points.cd),
        "glacier_code": (("cd",), points.glacier_code),
    },
)

box_size = 1000
half_box = box_size / 2
x_mins = xs - half_box
x_maxs = xs + half_box
y_mins = ys - half_box
y_maxs = ys + half_box

v_medians = []
v_error_medians = []

for i in range(len(x_mins)):
    x_slice = slice(x_mins[i], x_maxs[i])
    y_slice = slice(y_maxs[i], y_mins[i])

    subset = velocity.sel(x=x_slice, y=y_slice)

    v_median = subset["v"].median(dim=["x", "y"])
    v_error_median = subset["v_error"].median(dim=["x", "y"])

    v_medians.append(v_median)
    v_error_medians.append(v_error_median)

velocity_sampled["v_median"] = xr.concat(v_medians, dim="cd")
velocity_sampled["v_error_median"] = xr.concat(v_error_medians, dim="cd")
velocity_sampled["year"] = pd.to_datetime(velocity_sampled["year"] + 1985, format="%Y")

velocity_sampled["mapping"].attrs.update(velocity["mapping"].attrs)
velocity_sampled.attrs["crs"] = velocity.attrs.get("projection")
velocity_sampled.attrs["author"] = velocity.attrs.get("author")
velocity_sampled.attrs["institution"] = velocity.attrs.get("institution")
velocity_sampled.attrs["region"] = velocity.attrs.get("region")
velocity_sampled.attrs["title"] = velocity.attrs.get("title")

# velocity_sampled.to_netcdf("../data/velocity/velocity_points_1985_2022.nc")

velocity_sampled

-1895916.9014460526, 557131.4720849826; -1894916.9014460526, 558131.4720849826


100%|██████████| 162/162 [00:00<00:00, 261.86it/s]


<xarray.Dataset>
Dimensions:         (cd: 162, year: 38)
Coordinates:
    x               (cd) float64 5.576e+05 5.575e+05 ... 4.741e+05 4.74e+05
    y               (cd) float64 -1.895e+06 -1.896e+06 ... -2.437e+06 -2.437e+06
  * cd              (cd) int64 0 250 500 750 1000 ... 19250 19500 19750 20000
    glacier_code    (cd) object 'DJ' 'DJ' 'DJ' 'DJ' 'DJ' ... 'UI' 'UI' 'UI' 'UI'
  * year            (year) datetime64[ns] 1985-01-01 1986-01-01 ... 2022-01-01
Data variables:
    v_median        (cd, year) float32 dask.array<chunksize=(1, 1), meta=np.ndarray>
    v_error_median  (cd, year) float32 dask.array<chunksize=(1, 1), meta=np.ndarray>
    mapping         (year) <U1 '' '' '' '' '' '' '' '' ... '' '' '' '' '' '' ''
Attributes:
    crs:          3413
    author:       ITS_LIVE, a NASA MEaSUREs project (its-live.jpl.nasa.gov)
    institution:  NASA Jet Propulsion Laboratory (JPL), California Institute ...
    region:       RGI05A
    title:        ITS_LIVE annual mosaics of image pair velocities

In [209]:
import matplotlib.pyplot as plt
import pandas as pd
from matplotlib.dates import DateFormatter, YearLocator
from matplotlib.offsetbox import AnchoredText
from matplotlib.gridspec import GridSpec

GLACIERS = ["DJ", "UI"]
SETTINGS = {
    "DJ": {
        "colour": [(0.122, 0.467, 0.706, 1.0), (0.122, 0.467, 0.706, 0.25)],
        "label": "Daugaard-Jensen",
    },
    "UI": {
        "colour": [(1.0, 0.498, 0.055, 1.0), (1.0, 0.498, 0.055, 0.25)],
        "label": "Uunartit Islands",
    },
}

subset = velocity_sampled.sel(cd=1000)
years = subset["year"].values

# Global plot settings
plt.rcParams["figure.dpi"] = 1000
plt.rcParams["font.family"] = "Times New Roman"
plt.rcParams["font.size"] = 18
plt.rcParams["axes.labelsize"] = 18
plt.rcParams["xtick.labelsize"] = 18
plt.rcParams["ytick.labelsize"] = 18

fig = plt.figure(figsize=(16, 6))
gs = GridSpec(nrows=1, ncols=2, width_ratios=[1, 2], height_ratios=[1])
ax0 = fig.add_subplot(gs[0, 0])
ax1 = fig.add_subplot(gs[0, 1:])
ax = [ax0, ax1]

# Plot data on each subplot
for i, glacier in enumerate(GLACIERS):
    glacier_subset = subset.where(subset.glacier_code == glacier, drop=True)

    ax0_slice = slice(pd.to_datetime(1985, format="%Y"), pd.to_datetime(2010, format="%Y"))
    ax1_slice = slice(pd.to_datetime(2010, format="%Y"), pd.to_datetime(2024, format="%Y"))

    for j, slice_ in enumerate([ax0_slice, ax1_slice]):
        plot_v = glacier_subset["v_median"].sel(year=slice_).squeeze() / 1000
        plot_v_err = glacier_subset["v_error_median"].sel(year=slice_).squeeze() / 1000

        ax[j].errorbar(
            plot_v.year.values,
            plot_v.values,
            plot_v_err.values,
            label=SETTINGS[glacier]["label"],
            marker="o",
            linewidth=2.5,
            color=SETTINGS[glacier]["colour"][1],
            markersize=8,
            markeredgecolor=SETTINGS[glacier]["colour"][0],
            markerfacecolor=SETTINGS[glacier]["colour"][0],
            ecolor=SETTINGS[glacier]["colour"][1],
            elinewidth=5,
            zorder=10,
            clip_on=False,
        )

# Set y-axis range to fit data and adds label
ax[0].set_ylim(bottom=2, top=5.5)
ax[1].set_ylim(bottom=2, top=5.5)
ax[0].set_ylabel("Velocity [km y$^{-1}$]", labelpad=20)

# Set x-axis range to fit data
ax[0].set_xlim(pd.to_datetime("1985-01-01"), pd.to_datetime("2010-01-01"))
ax[1].set_xlim(pd.to_datetime("2010-01-01"), pd.to_datetime("2024-01-01"))

# Set x-axis tick frequency (major)
ax[0].xaxis.set_major_locator(YearLocator(base=5))
ax[0].xaxis.set_major_formatter(DateFormatter("%Y"))
ax[1].xaxis.set_major_formatter(DateFormatter("%Y"))

# Set x-axis tick frequency (minor)
ax[0].xaxis.set_minor_locator(YearLocator(1))
ax[1].xaxis.set_minor_locator(YearLocator(1))

# Rotate x-axis tick labels
ax[0].tick_params(axis="x", rotation=70)
ax[1].tick_params(axis="x", rotation=70)

# Disable y-axis tick labels
ax[1].tick_params(labelleft=False)

# Remove whitespace around data on plot
ax[0].margins(x=0)
ax[1].margins(x=0)

# Add plot labels and advance/retreat text
ax[0].add_artist(
    AnchoredText(
        "(c)",
        loc="upper left",
        borderpad=0.1,
        prop=dict(size=18, family="Times New Roman", weight="semibold", c="black"),
        frameon=False,
    )
)
ax[1].add_artist(
    AnchoredText(
        "(d)",
        loc="upper left",
        borderpad=0.1,
        prop=dict(size=18, family="Times New Roman", weight="semibold", c="black"),
        frameon=False,
    )
)

# Add gridlines
ax[0].grid(
    True,
    which="major",
    axis="both",
    c="gray",
    linestyle=":",
    linewidth=0.5,
    alpha=0.8,
    zorder=0,
)
ax[1].grid(
    True,
    which="both",
    axis="both",
    c="gray",
    linestyle=":",
    linewidth=0.5,
    alpha=0.8,
    zorder=0,
)

plt.tight_layout()
# plt.subplots_adjust(wspace=0.01)
# plt.savefig(
#     "../img/terminus_boxes_1985_2023_time-series.png",
#     dpi=fig.dpi,
#     bbox_inches="tight",
# )
plt.show()

## Plot sub-annual velocity time series

In [221]:
import json
from pathlib import Path
import s3fs as s3
import geopandas as gpd
from uuid import uuid4

import numpy as np
import xarray as xr
from shapely import geometry

DATACUBE_CATALOG_URL = "s3://its-live-data/datacubes/catalog_v02.json"
DATACUBE_CATALOG = {}
OPEN_CUBES = {}
VARIABLES = [
    "v",
    "v_error",
    "date_dt",
    "mid_date",
    "mission_img1",
    "satellite_img1",
    "acquisition_date_img1",
    "acquisition_date_img2",
]

s3fs = s3.S3FileSystem(anon=True)
with s3fs.open(DATACUBE_CATALOG_URL, "r") as catalog:
    DATACUBE_CATALOG = json.load(catalog)
    # DATACUBE_CATALOG = gpd.GeoDataFrame.from_features(datacube_catalog, crs=4326)


def find_by_point(lon, lat):
    cubes = []
    point = geometry.Point(lon, lat)

    for cube_feature in DATACUBE_CATALOG["features"]:
        cube_polygon = geometry.shape(cube_feature["properties"]["geometry_epsg"])

        if cube_polygon.contains(point):
            cubes.append(cube_feature)

    return cubes


def get_time_series(points):
    """
    For the points in the list, returns a list of dictionaries - each one containing:
        an xarray DataArray (time series) for each variable on the list for each of the lon lat points.

    :params points: List of (lon, lat) coordinates (EPSG:4326) (e.g. points along the center line of a glacier)
    :params variables: list of variables to be included in the Dataset: v, vx, vy etc.
    :returns: list of dictionaries with coordinates and xarray time series Datasets for the nearest neighbors to the points
                ITS_LIVE processes on a 120 m grid, so nearest points will be close to requested points
    """
    time_seriess = []
    for point in points:
        lon = point[0]
        lat = point[1]
        results = find_by_point(lon, lat)
        if len(results):
            cube = results[0]
            projection = cube["properties"]["epsg"]
            # print(projection)
            # for zarr store modify URL for use in boto open
            zarr_url = cube["properties"]["zarr_url"]
            cube_s3_url = zarr_url.replace("http:", "s3:").replace(".s3.amazonaws.com", "")
            projected_point = geometry.Point(lon, lat)
            # if we have already opened this cube, don't open it again
            if len(OPEN_CUBES) and cube_s3_url in OPEN_CUBES.keys():
                xr_da = OPEN_CUBES[cube_s3_url]
            else:
                xr_da = xr.open_dataset(
                    cube_s3_url, engine="zarr", storage_options={"anon": True}
                )
                OPEN_CUBES[cube_s3_url] = xr_da
            time_series = xr_da[VARIABLES].sel(
                x=projected_point.x, y=projected_point.y, method="nearest"
            )

            if time_series is not None and isinstance(time_series, xr.Dataset):
                x_off = time_series.x.values - projected_point.x
                y_off = time_series.y.values - projected_point.y

                time_seriess.append(
                    {
                        "returned_point_projected_coordinates": {
                            "epsg": projection,
                            "coords": (time_series.x.values, time_series.y.values),
                        },
                        "returned_point_offset_from_requested_in_projection_meters": np.sqrt(
                            x_off**2 + y_off**2
                        ),
                        "time_series": time_series,
                    }
                )

    return time_seriess


def export_csv(points, outdir=None):
    """Exports a list of ITS_LIVE glacier velocity variables to csv files"""

    outdir = f"./itslive-{uuid4()}" if outdir is None else outdir

    Path(outdir).mkdir(parents=True, exist_ok=True)

    for point in points:
        lon = round(point[0], 4)
        lat = round(point[1], 4)
        result_series = get_time_series([(lon, lat)])
        if len(result_series):
            series = result_series[0]["time_series"]

            df = series.to_dataframe()
            df["x"] = lon
            df["y"] = lat
            df = df.rename(
                columns={
                    "x": "lon",
                    "y": "lat",
                    "satellite_img1": "satellite",
                    "mission_img1": "mission",
                    "v": "v [m/yr]",
                    "v_error": "v_error [m/yr]",
                }
            )
            df["epsg"] = series.attrs["projection"]
            df["date_dt [days]"] = df["date_dt"].dt.days
            ts = df.dropna()
            file_name = f"LON{lon}--LAT{lat}.csv"
            ts.to_csv(
                f"{outdir}/{file_name}",
                columns=[
                    "lon",
                    "lat",
                    "v [m/yr]",
                    "v_error [m/yr]",
                    "date_dt [days]",
                    "mission",
                    "satellite",
                    "epsg",
                ],
            )


def export_netcdf(points, outdir=None):
    """Exports a list of ITS_LIVE glacier velocity variables to netcdf files"""

    outdir = f"./itslive-{uuid4()}" if outdir is None else outdir
    Path(outdir).mkdir(parents=True, exist_ok=True)

    for point in points:
        lon = round(point[0], 4)
        lat = round(point[1], 4)

        file_name = f"LON{lon}--LAT{lat}"
        result_series = get_time_series([(lon, lat)])
        if len(result_series):
            series = result_series[0]["time_series"]
            series.to_netcdf(f"{outdir}/{file_name}.nc")

In [287]:
# points_dj = [(-28.628460, 71.901442), (-28.774874, 71.832261), (-28.9666087, 71.7687319)]
# points_ui = [(-33.617543, 67.428825), (-33.804727, 67.419406), (-33.993418, 67.370211)]

points_dj = [(557070, -1896243), (554443, -1904793), (549937, -1913653)]
points_ui = [(488643, -2427221), (480919, -2429847), (473965, -2436845)]

velocities = get_time_series(points=points_ui)

print(f"{len(velocities)} time series found")

# Velocities is now an array with time series for each lat,lon pair
velocities[0]

3 time series found


{'returned_point_projected_coordinates': {'epsg': 3413,
  'coords': (array(488692.5), array(-2427172.5))},
 'returned_point_offset_from_requested_in_projection_meters': 69.3000721500346,
 'time_series': <xarray.Dataset>
 Dimensions:                (mid_date: 51837)
 Coordinates:
   * mid_date               (mid_date) datetime64[ns] 2019-07-12T14:00:21.1905...
     x                      float64 4.887e+05
     y                      float64 -2.427e+06
 Data variables:
     v                      (mid_date) float32 ...
     v_error                (mid_date) float32 ...
     date_dt                (mid_date) timedelta64[ns] 100 days 00:00:00 ... 2...
     mission_img1           (mid_date) <U1 ...
     satellite_img1         (mid_date) <U2 '2A' '2A' '7' '2A' ... '8' '7' '8' '8'
     acquisition_date_img1  (mid_date) datetime64[ns] ...
     acquisition_date_img2  (mid_date) datetime64[ns] ...
 Attributes: (12/19)
     Conventions:                CF-1.8
     GDAL_AREA_OR_POINT:         Area


In [290]:
dt = velocities[0]["time_series"]["date_dt"].values
dt = dt.astype(float) * 1.15741e-14
max_dt = 31
min_dt = 0
dt_mask = (dt >= min_dt) & (dt <= max_dt)


sats = velocities[0]["time_series"]["satellite_img1"].values
sat_mask = sats != "1A"

time_series = velocities[0]["time_series"].where(dt_mask)
time_series = time_series.where(sat_mask)

time_series

<xarray.DataArray 'v' ()>
array(11225.)
Coordinates:
    x        float64 4.887e+05
    y        float64 -2.427e+06

In [141]:
import matplotlib.pyplot as plt

plt.rcParams["figure.figsize"] = (16, 4)
fig, ax = plt.subplots()

color_index = 0

for vel in velocities:
    print(vel)
    latitude = float(vel["returned_point_projected_coordinates"]["coords"][0])
    longitude = float(vel["returned_point_projected_coordinates"]["coords"][1])

    point_label = f"Lon: {longitude}, Lat: {latitude}"
    vel["time_series"].v.plot(
        ax=ax,
        linestyle="None",
        marker="o",
        markersize=2,
        c=plt.cm.tab10(color_index),
        label=point_label,
        add_legend=True,
    )
    color_index += 1

plt.xlabel("Time")
plt.title("ITS_LIVE Velocity Profile")
ax.legend(loc="upper right")

{'returned_point_projected_coordinates': {'epsg': 3413, 'coords': (array(488692.5), array(-2427172.5))}, 'returned_point_offset_from_requested_in_projection_meters': 69.3000721500346, 'time_series': <xarray.Dataset>
Dimensions:                (mid_date: 51837)
Coordinates:
  * mid_date               (mid_date) datetime64[ns] 2019-07-12T14:00:21.1905...
    x                      float64 4.887e+05
    y                      float64 -2.427e+06
Data variables:
    v                      (mid_date) float32 ...
    v_error                (mid_date) float32 ...
    date_dt                (mid_date) timedelta64[ns] 100 days 00:00:00 ... 2...
    mission_img1           (mid_date) <U1 ...
    satellite_img1         (mid_date) <U2 ...
    acquisition_date_img1  (mid_date) datetime64[ns] 2019-05-23T14:00:21 ... ...
    acquisition_date_img2  (mid_date) datetime64[ns] 2019-08-31T14:00:21 ... ...
Attributes: (12/19)
    Conventions:                CF-1.8
    GDAL_AREA_OR_POINT:         Area
    aut

In [311]:
mid_dates = time_series["mid_date"].values
mid_dates_mask_a = (mid_dates >= pd.to_datetime("1985-01-01")) & (
    mid_dates <= pd.to_datetime("2010-01-01")
)
mid_dates_mask_b = (mid_dates >= pd.to_datetime("2010-01-01")) & (
    mid_dates <= pd.to_datetime("2024-01-01")
)

time_series_a = time_series.where(mid_dates_mask_a)
time_series_b = time_series.where(mid_dates_mask_b)

print(time_series_b)

<xarray.Dataset>
Dimensions:                (mid_date: 1902)
Coordinates:
  * mid_date               (mid_date) datetime64[ns] 1985-03-24T13:23:26.0603...
    x                      float64 4.887e+05
    y                      float64 -2.427e+06
Data variables:
    v                      (mid_date) float32 nan nan nan ... 4.607e+03 4.58e+03
    v_error                (mid_date) float32 nan nan nan ... 167.0 117.0 75.0
    date_dt                (mid_date) timedelta64[ns] NaT ... 16 days 00:00:0...
    mission_img1           (mid_date) object nan nan nan nan ... 'L' 'L' 'L' 'L'
    satellite_img1         (mid_date) object nan nan nan nan ... '8' '8' '9' '8'
    acquisition_date_img1  (mid_date) datetime64[ns] NaT ... 2022-10-18T13:41...
    acquisition_date_img2  (mid_date) datetime64[ns] NaT ... 2022-11-03T13:41...
Attributes: (12/19)
    Conventions:                CF-1.8
    GDAL_AREA_OR_POINT:         Area
    author:                     ITS_LIVE, a NASA MEaSUREs project (its-live.j

In [329]:
rolling_median_v = time_series_b["v"].rolling(mid_date=28, center=True).median()
rolling_median_v

time_series_b["rolling_b"] = rolling_median_v

rolling_median_v = time_series_a["v"].rolling(mid_date=28, center=True).median()
rolling_median_v

time_series_a["rolling_a"] = rolling_median_v

In [332]:
import matplotlib.pyplot as plt
import pandas as pd
from matplotlib.dates import DateFormatter, YearLocator, date2num
from matplotlib.offsetbox import AnchoredText
from matplotlib.gridspec import GridSpec
import datetime

GLACIERS = ["DJ", "UI"]
SETTINGS = {
    "DJ": {
        "colour": [(0.122, 0.467, 0.706, 1.0), (0.122, 0.467, 0.706, 0.25)],
        "label": "Daugaard-Jensen",
    },
    "UI": {
        "colour": [(1.0, 0.498, 0.055, 1.0), (1.0, 0.498, 0.055, 0.25)],
        "label": "Uunartit Islands",
    },
}

years = [int(i.split("_")[-2]) for i in annual_mosaics]
centreline_points = centreline_points[centreline_points["cd"] == 1000]

# Global plot settings
plt.rcParams["figure.dpi"] = 1000
plt.rcParams["font.family"] = "Times New Roman"
plt.rcParams["font.size"] = 18
plt.rcParams["axes.labelsize"] = 18
plt.rcParams["xtick.labelsize"] = 18
plt.rcParams["ytick.labelsize"] = 18

fig = plt.figure(figsize=(16, 6))
gs = GridSpec(nrows=1, ncols=2, width_ratios=[1, 2], height_ratios=[1])
ax0 = fig.add_subplot(gs[0, 0])
ax1 = fig.add_subplot(gs[0, 1:])
ax = [ax0, ax1]

glacier = "UI"

ax[0].errorbar(
    pd.to_datetime(time_series_a["mid_date"].values),
    time_series_a["v"],
    time_series_a["v_error"],
    label=SETTINGS[glacier]["label"],
    marker="o",
    linestyle="",
    markersize=3,
    markeredgecolor=SETTINGS[glacier]["colour"][0],
    markerfacecolor=SETTINGS[glacier]["colour"][0],
    ecolor=SETTINGS[glacier]["colour"][1],
    elinewidth=2,
    # zorder=10,
    # clip_on=False,
)

ax[1].errorbar(
    pd.to_datetime(time_series_b["mid_date"].values),
    time_series_b["v"],
    time_series_b["v_error"],
    label=SETTINGS[glacier]["label"],
    marker="o",
    linestyle="",
    markersize=3,
    markeredgecolor=SETTINGS[glacier]["colour"][0],
    markerfacecolor=SETTINGS[glacier]["colour"][0],
    ecolor=SETTINGS[glacier]["colour"][1],
    elinewidth=2,
    # zorder=10,
    # clip_on=False,
)

ax[0].plot(
    pd.to_datetime(time_series_a["mid_date"].values),
    time_series_a["rolling_a"],
    linestyle="-",
    c="black",
    zorder=10,
    # clip_on=False,
)

ax[1].plot(
    pd.to_datetime(time_series_b["mid_date"].values),
    time_series_b["rolling_b"],
    linestyle="-",
    c="black",
    zorder=10,
    # clip_on=False,
)

# Plot data on each subplot
for glacier in GLACIERS:
    glacier_data = centreline_points[centreline_points["glacier_code"] == glacier]

    for i, period in enumerate([years[:26], years[25:]]):
        plot_years = [pd.to_datetime(f"{y}-01-01") for y in period]
        plot_v = [float(glacier_data[f"{y}_v"].values) for y in period]
        plot_v_err = [float(glacier_data[f"{y}_v_err"].values) for y in period]
        ax[i].errorbar(
            plot_years,
            plot_v,
            plot_v_err,
            label=SETTINGS[glacier]["label"],
            marker="o",
            linewidth=2.5,
            color=SETTINGS[glacier]["colour"][1],
            markersize=8,
            markeredgecolor=SETTINGS[glacier]["colour"][0],
            markerfacecolor=SETTINGS[glacier]["colour"][0],
            ecolor=SETTINGS[glacier]["colour"][1],
            elinewidth=5,
            zorder=10,
            clip_on=False,
        )

# Set y-axis range to fit data and adds label
ax[0].set_ylim(bottom=1000, top=8000)
ax[1].set_ylim(bottom=1000, top=8000)
ax[0].set_ylabel("Velocity [km y$^{-1}$]", labelpad=20)

# Set x-axis range to fit data
ax[0].set_xlim(pd.to_datetime("1985-01-01"), pd.to_datetime("2010-01-01"))
ax[1].set_xlim(pd.to_datetime("2010-01-01"), pd.to_datetime("2024-01-01"))

# Set x-axis tick frequency (major)
ax[0].xaxis.set_major_locator(YearLocator(base=5))
ax[0].xaxis.set_major_formatter(DateFormatter("%Y"))
ax[1].xaxis.set_major_formatter(DateFormatter("%Y"))

# Set x-axis tick frequency (minor)
ax[0].xaxis.set_minor_locator(YearLocator(1))
ax[1].xaxis.set_minor_locator(YearLocator(1))

# Rotate x-axis tick labels
ax[0].tick_params(axis="x", rotation=70)
ax[1].tick_params(axis="x", rotation=70)

# Disable y-axis tick labels
ax[1].tick_params(labelleft=False)

# Remove whitespace around data on plot
ax[0].margins(x=0)
ax[1].margins(x=0)

# Add plot labels and advance/retreat text
ax[0].add_artist(
    AnchoredText(
        "(c)",
        loc="upper left",
        borderpad=0.1,
        prop=dict(size=18, family="Times New Roman", weight="semibold", c="black"),
        frameon=False,
    )
)
ax[1].add_artist(
    AnchoredText(
        "(d)",
        loc="upper left",
        borderpad=0.1,
        prop=dict(size=18, family="Times New Roman", weight="semibold", c="black"),
        frameon=False,
    )
)

# Add gridlines
ax[0].grid(
    True,
    which="major",
    axis="both",
    c="gray",
    linestyle=":",
    linewidth=0.5,
    alpha=0.8,
    zorder=0,
)
ax[1].grid(
    True,
    which="both",
    axis="both",
    c="gray",
    linestyle=":",
    linewidth=0.5,
    alpha=0.8,
    zorder=0,
)

plt.tight_layout()
# plt.subplots_adjust(wspace=0.01)
# plt.savefig(
#     "../img/terminus_boxes_1985_2023_time-series.png",
#     dpi=fig.dpi,
#     bbox_inches="tight",
# )
plt.show()

C:\Users\olive\AppData\Local\Temp\ipykernel_37208\1115324927.py:95: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  plot_v = [float(glacier_data[f"{y}_v"].values) for y in period]
C:\Users\olive\AppData\Local\Temp\ipykernel_37208\1115324927.py:96: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  plot_v_err = [float(glacier_data[f"{y}_v_err"].values) for y in period]
C:\Users\olive\AppData\Local\Temp\ipykernel_37208\1115324927.py:95: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 

## Plot variables as maps

In [ ]:
import xarray as xr
import matplotlib.pyplot as plt
import holoviews as hv
from bokeh.models import HoverTool
import geopandas as gpd

# Define the coordinates for the bounding box
bbox_y_min = -1866831
bbox_x_min = -312651
bbox_y_max = -1799771
bbox_x_max = -260844

centreline_points = gpd.read_file("../data/misc/centreline_points.geojson")
centreline_lines = gpd.read_file("../data/misc/centreline_lines.geojson")
centreline_dj = centreline_lines[centreline_lines["glacier_code"] == "DJ"]

bbox_x_min, bbox_y_min, bbox_x_max, bbox_y_max = centreline_dj.bounds.values[0]

mosaic_path = "..\\data\\velocity\\ITS_LIVE_velocity_120m_RGI05A_2022_v02.nc"

with xr.open_dataset(mosaic_path, engine="h5netcdf") as ds:
    # Step 1: Determine the dataset's extent
    x_min = ds["x"].min().item()  # Get minimum 'x' coordinate
    x_max = ds["x"].max().item()  # Get maximum 'x' coordinate
    y_min = ds["y"].min().item()  # Get minimum 'y' coordinate
    y_max = ds["y"].max().item()  # Get maximum 'y' coordinate

    print(f"Dataset extent: x = [{x_min}, {x_max}], y = [{y_min}, {y_max}]")

    # Slice the dataset with the updated bounding box
    ds_subset = ds.where(
        (ds["x"] >= bbox_x_min)
        & (ds["x"] <= bbox_x_max)
        & (ds["y"] >= bbox_y_min)
        & (ds["y"] <= bbox_y_max),
        drop=True,
    )

    # Optionally clip dataset to land ice mask
    landice_mask = ds_subset["landice"] > 0
    ds_subset = ds_subset.where(landice_mask, float("nan"))

    # Optional: Plot the subsetted data
    ds_subset["v"].plot(cmap="viridis")
    plt.title("v")
    plt.show()

    ds_subset["v_error"].plot(cmap="viridis")
    plt.title("v_error")
    plt.show()

    ds_subset["landice"].plot(cmap="viridis")
    plt.title("landice")
    plt.show()

    ds_subset["floatingice"].plot(cmap="viridis")
    plt.title("floatingice")
    plt.show()

    ds_subset["count"].plot(cmap="viridis")
    plt.title("count")
    plt.show()

# Datacube access & sampling

In [ ]:
import json
import logging

import geopandas as gpd
import numpy as np
import pandas as pd
import s3fs as s3
import xarray as xr

logging.basicConfig()
logger = logging.getLogger(__name__)
logger.setLevel(logging.INFO)


def get_datacube_instances(points):
    """Identifies the ITS_LIVE Zarr datacubes corresponding to sampling points.

    Parameters
    ----------
    points : geopandas.GeoDataFrame
        GeoDataFrame containing points along a glacier centreline.

    Returns
    -------
    datacubes : list of str
        List unique datacube URLs.
    points : geopandas.GeoDataFrame
        points with corresponding datacube URL appended.

    See also
    --------
    sample_datacubes
    """

    # Reads ITS_LIVE Zarr datacube catalog as GeoDataFrame
    s3fs = s3.S3FileSystem(anon=True)
    catalog_url = "s3://its-live-data/datacubes/catalog_v02.json"
    with s3fs.open(catalog_url, "r") as datacube_catalog:
        datacube_catalog = json.load(datacube_catalog)
        datacube_catalog = gpd.GeoDataFrame.from_features(datacube_catalog, crs=4326)

    # Intersects points with datacube outlines
    points = (
        points.to_crs(4326)
        .overlay(datacube_catalog[["geometry", "zarr_url"]], how="intersection")
        .set_index(["glacier", "cd"])
        .to_crs(3413)
    )

    # Amends URLs
    points["zarr_url"] = (
        points["zarr_url"].str.replace("http:", "s3:").str.replace(".s3.amazonaws.com", "")
    )

    # Creates list of unique datacubes (as their URLs)
    datacubes = points["zarr_url"].unique().tolist()
    logger.info(f"Number of unique datacubes: {len(datacubes)}")

    return datacubes, points


def sample_datacubes(datacubes, points, spatial_averaging=True):
    """Samples ITS_LIVE Zarr datacube at points.

    Parameters
    ----------
    datacubes : list of str
        List unique datacube URLs.
    points : geopandas.GeoDataFrame
        GeoDataFrame containing points along a glacier centreline.
    spatial_averaging : bool
        Flag to sample in a 3x3 window around each point [default=True].

    Returns
    -------
    datasets : list of xarray.Dataset
        Sampled datasets with the dimensions:
            - mid_date  ...
            - glacier   ...
            - cd        binned distance along centreline
            - k         int (0-8) each point in the 3x3 kernel

    See also
    --------
    get_datacube_instances
    """

    # Creates storage needed for spatial averaging, if necessary
    if spatial_averaging:
        points["windows"] = pd.Series(dtype=object)

    # Creates storage for sampled datasets
    datasets = []

    for dc_url in datacubes:
        print(points.to_string())

        # Gets index of points within current the datacube
        z_idx = points["zarr_url"] == dc_url

        with xr.open_dataset(dc_url, engine="zarr", storage_options={"anon": True}) as dc:
            if not spatial_averaging:
                # Gets point x and y coords
                point_x = points.loc[z_idx, "x"].to_xarray()
                point_y = points.loc[z_idx, "y"].to_xarray()
                mask = ~np.isnan(point_x)

                # Queries datacube at point
                dc = dc.sel(x=point_x, y=point_y, method="nearest").sortby("mid_date")

            else:
                # Creates additional points for 3x3 kernal about each index
                diffs_x = np.abs(points.loc[z_idx, "x"].values - dc["x"].values[:, np.newaxis])
                diffs_y = np.abs(points.loc[z_idx, "y"].values - dc["y"].values[:, np.newaxis])
                x_idx = diffs_x.argmin(axis=0)
                y_idx = diffs_y.argmin(axis=0)
                windows = []
                for x, y in list(zip(x_idx, y_idx)):
                    window = []
                    for y_ in [y + 1, y, y - 1]:
                        for x_ in [x - 1, x, x + 1]:
                            window.append((x_, y_))
                    windows.append(window)

                # Appends window indicies to points GeoDataFrame
                points.loc[z_idx, "windows"] = pd.Series(
                    windows, index=points.loc[z_idx].index
                )

                # Unpacks list of windows
                query = (
                    points.loc[z_idx, "windows"]
                    .apply(pd.Series)
                    .reset_index()
                    .melt(["glacier", "cd"])
                    .sort_values(by=["glacier", "cd"])
                    .rename(columns={"variable": "k", "value": "idx"})
                    .set_index(["glacier", "cd", "k"])
                )

                # Unpacks each window's tuple
                query = query["idx"].apply(pd.Series).rename(columns={0: "x_idx", 1: "y_idx"})

                # Removes invalid indicies caused when points cross a datacube boundary
                invalid = (
                    (query["y_idx"] >= len(dc["y"]))
                    | (query["y_idx"] < 0)
                    | (query["x_idx"] >= len(dc["x"]))
                    | (query["x_idx"] < 0)
                )
                query = query[~invalid]

                # Gets point x and y coords
                point_x = query["x_idx"].to_xarray()
                point_y = query["y_idx"].to_xarray()
                mask = ~np.isnan(point_x)

                # Handles NaN values created when dealing with centrelines of differing length
                point_x = xr.where(mask, point_x, 0).astype(int)
                point_y = xr.where(mask, point_y, 0).astype(int)

                # Queries datacube at point
                dc = dc.isel(x=point_x, y=point_y).sortby("mid_date")

            # Masks NaN values
            dc["x"] = xr.where(mask, dc["x"], np.nan)
            dc["y"] = xr.where(mask, dc["y"], np.nan)
            dc["mask"] = mask

            logger.info(f"Datacube dimensions: {dc.dims}")
            datasets.append(dc.chunk(chunks={"cd": 15, "glacier": 1}))

    logger.info(f"Number of datacubes loaded: {len(datasets)}")

    return datasets


def get_time_series(datasets, start_d, stop_d, distances, date_dt_max="30D"):
    """Gets velocity time series at points and resamples them to regular frequencies.

    Parameters
    ----------
    datasets : list of xarray.Dataset
        Sampled IT_LIVE data.
    start_d : str
        pandas timedelta string for filtering on mid_date.
    stop_d : str
        pandas timedelta string for filtering on mid_date.
    distances : list
        list of distances along centreline (cd) to include.
    date_dt_max : str
        pandas timedelta string specifying maximum date_dt [default=30].


    Returns
    -------
    v_time_series : pandas.DataFrame
        DataFrame of velocities that meet date, date_dt, and cd filter requirements.
            - glacier, cd, mid_date [with frequency = resample_frequency), v, season, year

    See also
    --------
    error_weighted_average
    get_seasonal_averages
    get_time_series
    v_uncertainty
    """

    filtered = []

    for ds in datasets:
        d_idx = ds["mid_date"].to_pandas().between(start_d, stop_d)
        date_dt_idx = ds["date_dt"] <= pd.Timedelta(date_dt_max)
        mid_date_idx = date_dt_idx & d_idx
        cd_idx = ds["cd"].isin(distances)

        if "k" not in list(ds.dims):  # then spatial averaging
            average_v, average_v_error = v_uncertainty(
                ds["vx"][mid_date_idx, :, cd_idx],
                ds["vy"][mid_date_idx, :, cd_idx],
                ds["vx_error"][mid_date_idx],
                ds["vy_error"][mid_date_idx],
            )
        else:
            average_vx = ds["vx"][mid_date_idx, :, cd_idx, :].mean(dim="k", skipna=True)
            average_vy = ds["vy"][mid_date_idx, :, cd_idx, :].mean(dim="k", skipna=True)
            average_v, average_v_error = v_uncertainty(
                average_vx,
                average_vy,
                ds["vx_error"][mid_date_idx],
                ds["vy_error"][mid_date_idx],
            )

        filtered.append(
            xr.merge(
                [
                    average_v.rename("v"),
                    average_v_error.rename("v_error"),
                    ds[
                        [
                            "acquisition_date_img1",
                            "acquisition_date_img2",
                            "date_dt",
                            "satellite_img1",
                            "mission_img1",
                        ]
                    ].sel(mid_date=mid_date_idx),
                ]
            )
        )

    print(filtered)

    # Concatenate datasets along the mid_date dimension
    concatenated = xr.concat(filtered, dim="mid_date", combine_attrs="override")

    # Convert to DataFrame and drop duplicates based on mid_date
    concatenated_df = concatenated.to_dataframe().reset_index()
    concatenated_df = concatenated_df.drop_duplicates(subset=["mid_date", "glacier", "cd"])

    # Filter out NaN values in 'v'
    v_time_series_df = concatenated_df[~concatenated_df["v"].isna()]

    # 28-day rolling median
    rolling_median = (
        v_time_series_df.set_index("mid_date")
        .groupby(["glacier", "cd"])["v"]
        .rolling("28D")
        .median()
        .rename("smoothed_v")
        .reset_index()
    )

    v_time_series_df = v_time_series_df.merge(
        rolling_median, on=["mid_date", "glacier", "cd"], how="left"
    )

    # Calculate intermediate steps for error-weighted averages
    v_time_series_df["v_over_sigma2"] = v_time_series_df["v"] / (
        v_time_series_df["v_error"] ** 2
    )
    v_time_series_df["one_over_sigma2"] = 1 / (v_time_series_df["v_error"] ** 2)

    return v_time_series_df